In [241]:
import os
import openai

from dotenv import load_dotenv, find_dotenv
_ = load_dotenv(find_dotenv()) # read local .env file

azure_openai_api_key = os.getenv('AZURE_OPENAI_API_KEY_4')
azure_openai_endpoint = os.getenv('AZURE_OPENAI_API_ENDPOINT_4')
deployment_name = os.getenv('AZURE_DEPLOYMENT_NAME_4')


# Set up Azure OpenAI API (for Azure deployment)
openai.api_type = "azure"
openai.api_key = azure_openai_api_key
openai.api_base = azure_openai_endpoint
openai.api_version = "2023-05-15"  # Ensure this is up to date

import warnings
warnings.filterwarnings('ignore')

In [242]:
from langchain.chat_models import ChatOpenAI
from langchain.prompts import ChatPromptTemplate
from langchain_core.runnables import RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser
from langchain.chat_models import AzureChatOpenAI
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.document_loaders import CSVLoader
from langchain_community.vectorstores import FAISS
from langchain.schema import Document
import pandas as pd

In [244]:
llm = AzureChatOpenAI(
    api_key=azure_openai_api_key,  # Azure OpenAI API Key
    api_version="2023-12-01-preview",  # API version (you can adjust it as needed)
    azure_endpoint=azure_openai_endpoint,  # Azure OpenAI endpoint
    deployment_name=deployment_name,  # Ensure deployment_name is the correct one you configured in Azure
    temperature=0  # Optional: Adjust the temperature for randomness in responses
)

AttributeError: module 'openai' has no attribute 'AzureOpenAI'

In [4]:
csv_path = "../../RGBD/table_produits/produits.csv"   # Remplace avec le chemin réel si besoin
df = pd.read_csv(csv_path, encoding='utf-8')
df.columns

Index(['url', 'nom_produit', 'img_produit', 'prix_produit', 'contenance',
       'pg_vg', 'origine', 'frais', 'surbooste', 'saveur', 'description',
       'brand', 'gout', 'info_brand', 'id_produit'],
      dtype='object')

enregistrer le saveur et le id_produit dans le metadata du doc

In [178]:
# Charger le CSV
csv_path = "../../RGBD/table_produits/produits.csv"   # Remplace avec le chemin réel si besoin
df = pd.read_csv(csv_path, encoding='utf-8')

# Vérifier que la colonne "description" existe bien
if "description" not in df.columns:
    raise ValueError("La colonne 'description' n'existe pas dans le CSV ! Vérifie le nom des colonnes.")
# Vérification de la colonne "id_produit"
if "id_produit" not in df.columns:
    raise ValueError("La colonne 'id_produit' n'existe pas dans le CSV ! Vérifiez le nom des colonnes.")

# Transformer chaque ligne en objet Document avec métadonnées
documents = []
for index, row in df.iterrows():
    metadata = {"source": csv_path, "row": index,"id_produit": row["id_produit"]}

    if "saveur" in row:
        metadata["saveur"] = str(row["saveur"])  # Ajouter la saveur dans les métadonnées

    documents.append(Document(page_content=str(row["description"]), metadata=metadata))

print(f"Nombre de documents préparés : {len(documents)}")

Nombre de documents préparés : 1531


In [179]:
# Charger le CSV
csv_path = "../../RGBD/table_produits/produits.csv"   # Remplace avec le chemin réel si besoin
df = pd.read_csv(csv_path, encoding='utf-8')

# Vérifier que la colonne "description" existe bien
if "description" not in df.columns:
    raise ValueError("La colonne 'description' n'existe pas dans le CSV ! Vérifie le nom des colonnes.")
# Vérification de la colonne "id_produit"
if "id_produit" not in df.columns:
    raise ValueError("La colonne 'id_produit' n'existe pas dans le CSV ! Vérifiez le nom des colonnes.")

# Transformer chaque ligne en objet Document avec métadonnées
documents = []
for index, row in df.iterrows():
    metadata = {"source": csv_path, "row": index, "id_produit": row["id_produit"]}

    # Ajouter les métadonnées supplémentaires si elles existent dans le DataFrame
    if "saveur" in row:
        metadata["saveur"] = str(row["saveur"])
    if "pg_vg" in row:
        metadata["pg_vg"] = str(row["pg_vg"])
    if "origine" in row:
        metadata["origine"] = str(row["origine"])
    if "frais" in row:
        metadata["frais"] = str(row["frais"])
    if "surbooste" in row:
        metadata["surbooste"] = str(row["surbooste"])
    if "brand" in row:
        metadata["brand"] = str(row["brand"])
    if "gout" in row:
        metadata["gout"] = str(row["gout"])

    documents.append(Document(page_content=str(row["description"]), metadata=metadata))

print(f"Nombre de documents préparés : {len(documents)}")


Nombre de documents préparés : 1531


In [180]:
documents

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 0, 'id_produit': 1, 'saveur': 'cassis, lime, fruits rouges, parfait', 'pg_vg': '50/50', 'origine': 'France', 'frais': 'Oui', 'surbooste': 'Non', 'brand': 'Arômes et Liquides (A&L)', 'gout': 'fruit'}, page_content="Le e-liquide Ragnarok par A&L Ultimate est un produitprêt à l'emploipour cigarette électronique. Dans sa fiole 10ml, vous retrouverez des saveurs de fruits rouges, accompagnées d'un goût frais de cassis. Idéal pour débuter, ce e-liquide vous est proposé en différents taux de nicotine au choix : 0, 3, 6, ou 12mg/ml. Qu'est-ce que le Ragnarok Ultimate ? Le Ragnarok, c'est unerecette fraiche aux goûts de fruitsdehaute qualité française, signée Arômes et Liquides (A&L). Ici, vous en profiterez dans sa version e-liquide prêt à vaper. Conforme à la loi TPD, le e liquide Ragnarok est présenté en fiole PET de 10ml. Pourquoi ? Afin de vous assurer unproduit déjà nicotiné à votre convenance! Pourquoi choisir

In [6]:
# Étape 3: Création et sauvegarde du vecteur FAISS avec métadonnées
embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")
try:
    vectorstore = FAISS.from_documents(documents, embeddings)
    vectorstore.save_local('faiss_vector_store')
    print("Vector store enregistré avec succès !")
except Exception as e:
    print(f"Erreur lors de la création du vectorstore : {e}")

C:\Users\antoa\AppData\Local\Temp\ipykernel_45072\4037170700.py:2: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")


KeyboardInterrupt: 

k 10

In [ ]:
retriever = vectorstore.as_retriever(
    search_type="similarity",  # Recherche des voisins les plus proches
    search_kwargs={
        "k": 10,  # Retourne les 3 voisins les plus proches
    }
)

In [85]:
query = "Quel produit contient des saveurs fraise et bonbon ?"

In [16]:
retriever.invoke(query)

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [24]:
results = retriever.invoke(query)
# Initialiser une liste pour stocker les id_produit
id_produits_list = []

# Parcourir les résultats et récupérer le 'id_produit' dans les métadonnées
for doc in results:
    # Vérifier si 'id_produit' est dans les métadonnées du document
    if 'id_produit' in doc.metadata:
        id_produits_list.append(doc.metadata['id_produit'])

# Afficher la liste des id_produits
id_produits_list

[855, 1261, 464, 797, 844, 921, 940, 652, 822, 541]

In [25]:
user_relevant_ids = [464, 797, 921, 464, 855]

In [26]:
# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produits_list, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 40.00%


avec k 5

In [27]:
retriever = vectorstore.as_retriever(
    search_type="similarity",  # Recherche des voisins les plus proches
    search_kwargs={
        "k": 5
    }
)

In [29]:
retriever.invoke(query)

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [28]:
results = retriever.invoke(query)
# Initialiser une liste pour stocker les id_produit
id_produits_list = []

# Parcourir les résultats et récupérer le 'id_produit' dans les métadonnées
for doc in results:
    # Vérifier si 'id_produit' est dans les métadonnées du document
    if 'id_produit' in doc.metadata:
        id_produits_list.append(doc.metadata['id_produit'])

# Afficher la liste des id_produits
id_produits_list

[855, 1261, 464, 797, 844]

In [30]:
user_relevant_ids = [797, 844, 464]

In [31]:
# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produits_list, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 60.00%


parametre cosin 

In [34]:
retriever = vectorstore.as_retriever(
    search_type="similarity",
    search_kwargs={
        
        "distance_metric": "cosine"
    }
)


In [35]:
retriever.invoke(query)

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [36]:
results = retriever.invoke(query)
# Initialiser une liste pour stocker les id_produit
id_produits_list = []

# Parcourir les résultats et récupérer le 'id_produit' dans les métadonnées
for doc in results:
    # Vérifier si 'id_produit' est dans les métadonnées du document
    if 'id_produit' in doc.metadata:
        id_produits_list.append(doc.metadata['id_produit'])

# Afficher la liste des id_produits
id_produits_list

[855, 1261, 464, 797]

In [37]:
user_relevant_ids = [797, 464]

# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produits_list, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 50.00%


"include_metadata": True

In [44]:
retriever = vectorstore.as_retriever(
    search_type="similarity",
    search_kwargs={
        "k": 10,
        "include_metadata": True
    }
)


In [45]:
retriever.invoke(query)

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [46]:
results = retriever.invoke(query)
# Initialiser une liste pour stocker les id_produit
id_produits_list = []

# Parcourir les résultats et récupérer le 'id_produit' dans les métadonnées
for doc in results:
    # Vérifier si 'id_produit' est dans les métadonnées du document
    if 'id_produit' in doc.metadata:
        id_produits_list.append(doc.metadata['id_produit'])

user_relevant_ids = [797, 464, 844, 921, ]

# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produits_list, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 40.00%


      "max_score": 0.95

In [50]:
retriever = vectorstore.as_retriever(
    search_type="similarity",
    search_kwargs={
        "k": 6,
        "max_score": 0.95
    }
)
retriever.invoke(query)

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [51]:
results = retriever.invoke(query)
# Initialiser une liste pour stocker les id_produit
id_produits_list = []

# Parcourir les résultats et récupérer le 'id_produit' dans les métadonnées
for doc in results:
    # Vérifier si 'id_produit' est dans les métadonnées du document
    if 'id_produit' in doc.metadata:
        id_produits_list.append(doc.metadata['id_produit'])

user_relevant_ids = [797, 464, 844, 921]

# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produits_list, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 66.67%


"filters": {"saveur": flavors_in_query}

In [52]:
# Fonction pour extraire les saveurs de la requête et les rechercher dans les résultats
def extract_flavors_from_query(query):
    """
    Cette fonction extrait les saveurs présentes dans la requête `query`
    et retourne une liste des saveurs trouvées parmi celles définies dans `flavor_list`.
    """
    # Liste des saveurs disponibles
    flavor_list = ["cassis", "lime", "fraise", "menthe", "mangue", "pêche", "bonbon"]

    found_flavors = []
    
    # Pour chaque saveur de la liste, vérifier si elle est mentionnée dans la requête
    for flavor in flavor_list:
        if re.search(rf'\b{flavor}\b', query, re.IGNORECASE):
            found_flavors.append(flavor)

    return found_flavors


# Fonction pour interroger le vecteur et récupérer les saveurs associées à la requête
def search_for_flavor(query):
    # Extraire les saveurs mentionnées dans la requête
    flavors_in_query = extract_flavors_from_query(query)

    # Afficher uniquement les saveurs extraites
    print(f"Saveurs extraites de la requête : {flavors_in_query}")

    # Retourner les saveurs extraites sous forme de chaîne, séparées par des virgules
    return ", ".join(flavors_in_query)



# Utilisation de la fonction search_for_flavor dans retriever.invoke
flavors_in_query = search_for_flavor(query)

Saveurs extraites de la requête : ['fraise', 'bonbon']


In [55]:
retriever = vectorstore.as_retriever(
    search_type="similarity",
    search_kwargs={
        "k": 6,
        "filters": {"saveur": flavors_in_query}
    }
)
retriever.invoke(query)



[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [56]:
results = retriever.invoke(query)
# Initialiser une liste pour stocker les id_produit
id_produits_list = []

# Parcourir les résultats et récupérer le 'id_produit' dans les métadonnées
for doc in results:
    # Vérifier si 'id_produit' est dans les métadonnées du document
    if 'id_produit' in doc.metadata:
        id_produits_list.append(doc.metadata['id_produit'])

user_relevant_ids = [797, 464, 844, 921]

# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produits_list, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 66.67%


In [71]:
retriever = vectorstore.as_retriever(
    search_type="similarity",
    search_kwargs={
        "k": 6,  # Retourne les 5 voisins les plus proches
        "distance_metric": "cosine",  # Utilise la similarité cosinus
        "include_metadata": True,  # Inclut les métadonnées dans les résultats
        "min_score": 0.8,  # Seuil de score minimum
        "filters": {"saveur": flavors_in_query}
    }
)
retriever.invoke(query)

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [65]:
results = retriever.invoke(query)
# Initialiser une liste pour stocker les id_produit
id_produits_list = []

# Parcourir les résultats et récupérer le 'id_produit' dans les métadonnées
for doc in results:
    # Vérifier si 'id_produit' est dans les métadonnées du document
    if 'id_produit' in doc.metadata:
        id_produits_list.append(doc.metadata['id_produit'])

user_relevant_ids = [797, 464, 844]

# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produits_list, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 60.00%


In [78]:
retriever = vectorstore.as_retriever(
    search_type="similarity",
    search_kwargs={
        "k": 6,
        "max_distance": 0.1  # Limite les résultats aux voisins dans une distance de 0.5
    }
)
retriever.invoke(query)

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [79]:
results = retriever.invoke(query)
# Initialiser une liste pour stocker les id_produit
id_produits_list = []

# Parcourir les résultats et récupérer le 'id_produit' dans les métadonnées
for doc in results:
    # Vérifier si 'id_produit' est dans les métadonnées du document
    if 'id_produit' in doc.metadata:
        id_produits_list.append(doc.metadata['id_produit'])

user_relevant_ids = [797, 464, 844, 921]

# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produits_list, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 66.67%


In [83]:
from langchain.embeddings import HuggingFaceEmbeddings
from transformers import AutoTokenizer, AutoModel

In [86]:
# Charger le modèle Hugging Face et le tokenizer
tokenizer = AutoTokenizer.from_pretrained('bert-base-uncased')
model = AutoModel.from_pretrained('bert-base-uncased')

# Créer l'objet HuggingFaceEmbeddings
embeddings = HuggingFaceEmbeddings(model_name="bert-base-uncased")

# Calculer l'embedding de la requête
query_embedding = embeddings.embed_documents([query])

# Afficher l'embedding
print(query_embedding)

No sentence-transformers model found with name bert-base-uncased. Creating a new one with mean pooling.


[[-0.34016695618629456, -0.07569482177495956, -0.45105913281440735, -0.12202954292297363, 0.2912018895149231, -0.015760131180286407, 0.2883029878139496, 0.6658528447151184, -0.07388688623905182, -0.6114656329154968, -0.1296709030866623, -0.11382053047418594, -0.3158952593803406, 0.6097073554992676, -0.7720197439193726, 0.7256824970245361, 0.38845136761665344, -0.12910397350788116, -0.006191160995513201, -0.2524934709072113, -0.26795652508735657, -0.01579357497394085, -0.7448946833610535, 0.017159098759293556, 0.2659573554992676, 0.009683621115982533, 0.0707121416926384, 0.16220471262931824, 0.006900880020111799, 0.4237213134765625, 0.16587059199810028, 0.6552513241767883, -0.3917093873023987, -0.349073588848114, -0.03998929634690285, 0.06876463443040848, 0.26459258794784546, 0.24970968067646027, -0.2143535166978836, 0.3324318826198578, -0.7526648640632629, -0.6961387991905212, -0.07627291232347488, 0.00035095843486487865, -0.4589574635028839, -0.4336487650871277, 0.5001071095466614, -0

In [87]:
retriever.invoke(query)

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [88]:
results = retriever.invoke(query)
# Initialiser une liste pour stocker les id_produit
id_produits_list = []

# Parcourir les résultats et récupérer le 'id_produit' dans les métadonnées
for doc in results:
    # Vérifier si 'id_produit' est dans les métadonnées du document
    if 'id_produit' in doc.metadata:
        id_produits_list.append(doc.metadata['id_produit'])

user_relevant_ids = [797, 464, 844, 921]

# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produits_list, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 66.67%


In [ ]:
retriever = vectorstore.as_retriever(
    search_type="similarity",
    search_kwargs={
        "k": 5,  # Retourne les 5 voisins les plus proches
        "query_embedding": query_embedding[0]  # Embedding pré-calculé de la requête
    }
)

In [17]:


# Fonction pour extraire les saveurs de la requête
def extract_flavors_from_query(query):
    flavor_list = ["cassis", "lime", "fraise", "menthe", "mangue", "pêche", "bonbon"]
    found_flavors = []

    # Pour chaque saveur dans la liste, vérifier si elle est mentionnée dans la requête
    for flavor in flavor_list:
        if re.search(rf'\b{flavor}\b', query, re.IGNORECASE):
            found_flavors.append(flavor)

    return found_flavors

# Fonction principale de recherche avec filtrage post-retrieval
def search_for_flavor_with_other_flavors(query, vectorstore):
    # Extraire les saveurs mentionnées dans la requête
    flavors_in_query = extract_flavors_from_query(query)

    if not flavors_in_query:
        print("Aucune saveur mentionnée dans la requête.")
        return []

    print(f"Saveurs extraites de la requête : {flavors_in_query}")

    # Paramétrer le retriever pour la recherche par similarité
    retriever = vectorstore.as_retriever(
        search_type="similarity",  # Recherche des voisins les plus proches
        search_kwargs={
            "k": 10,  # Retourner les 10 voisins les plus proches
        }
    )

    # Effectuer la recherche dans le vectorstore
    results = retriever.invoke(query)

    # Filtrage des résultats pour ne garder que ceux contenant les saveurs mentionnées
    filtered_results = []
    for result in results:
        # Vérifier si la saveur de la requête est présente dans les résultats
        product_flavors = result.metadata.get('saveur', '').lower().split(', ')
        if any(flavor.lower() in product_flavors for flavor in flavors_in_query):
            filtered_results.append(result)

    # Si aucun produit n'est trouvé avec les saveurs de la requête, renvoyer tous les résultats
    if not filtered_results:
        filtered_results = results

    # Retourner les résultats filtrés
    return filtered_results


In [20]:
results = search_for_flavor_with_other_flavors(query, vectorstore)

Saveurs extraites de la requête : ['fraise', 'bonbon']


In [21]:
recommended_ids = [rec.metadata["id_produit"] for rec in results]
recommended_ids


[855, 464, 797, 844, 921, 822]

In [22]:
user_relevant_ids = [844, 921, 797, 464, 855]

In [23]:
# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(recommended_ids, user_relevant_ids)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 83.33%


In [100]:
retriever = vectorstore.as_retriever(
    search_type="similarity_score_threshold",
    search_kwargs={"score_threshold": 0.3}
)

In [112]:
retriever = vectorstore.as_retriever(
    search_type="similarity",  # Recherche des voisins les plus proches
    search_kwargs={
        "k": 10,  # Retourne les 3 voisins les plus proches
    }
)

In [114]:
# Définition du prompt pour la génération de réponse
prompt_template = """
You are an assistant for question-answering tasks.
Use the following pieces of retrieved context to answer the question.
If you don't know the answer, just say that you don't know.

Question: {question}

Context: {context}

Answer:
"""

# Initialisation du prompt
prompt = ChatPromptTemplate.from_template(prompt_template)

# Formatage des documents de contexte
def format_docs(flavors):  # La fonction attend un argument 'flavors'
    # Création du contexte avec les saveurs extraites
    return f"Les saveurs extraites sont : {flavors}"

# Vous devez ici utiliser la variable `flavors_in_query` pour formater le texte
formatted_docs = format_docs(flavors_in_query)  # Utiliser `flavors_in_query` directement

# Pipeline de question-réponse
qa_chain = (
    {
        "context": retriever | format_docs,  # Utilisation du retriever pour obtenir des contextes
        "question": RunnablePassthrough(),
    }
    | prompt
    | llm
    | StrOutputParser()  # Extraction de la réponse
)

# Exécution de la chaîne de question-réponse et affichage du résultat
# Ici, tu passes les saveurs extraites en tant que contexte dans le modèle
response = qa_chain.invoke(query) #, filter={"saveur": flavors_in_query})

In [115]:
response

'Le produit qui contient des saveurs de fraise et de bonbon est le "Fraise Candy", un e-liquide fabriqué par Prestige Fruits pour la gamme Sweety Fruits.'

In [117]:
# Définition du prompt pour la génération de réponse avec métadonnées explicites
prompt_template = """
Tu es un assistant qui reponde aux questions de l'user. 
Fournissez la réponse suivante accompagnée des métadonnées des produits, y compris 'id_produit'.
Tu vas retourner plusieurs reponses.

Question: {question}

Context: {context}

Reponse: id_produit=<id_produit_value>; [Additional product details here]
"""

# Initialisation du prompt
prompt = ChatPromptTemplate.from_template(prompt_template)

# Pipeline de question-réponse
qa_chain = (
    {
        "context": retriever | format_docs,  # Utilisation du retriever pour obtenir des contextes
        "question": RunnablePassthrough(),
    }
    | prompt
    | llm
    | StrOutputParser()  # Extraction de la réponse
)

# Exécution de la chaîne de question-réponse
response = qa_chain.invoke(query) #, filter={"saveur": flavors_in_query})

# Exemple de réponse, elle pourrait contenir les métadonnées (par exemple id_produit)
print(response)


Voici les produits qui contiennent des saveurs de fraise et de bonbon :

1. **Produit 1**
   - **id_produit**: 464
   - **Détails**: Ce produit de la marque Snapple propose un mélange de saveurs fruitées et de bonbons, incluant la fraise et la barbe à papa. Il est fabriqué en France et se compose d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG), avec un ratio de 50PG/50VG.

2. **Produit 2**
   - **id_produit**: 797
   - **Détails**: Le Freho Extra Frais 50ml est un e-liquide à booster fabriqué par e.Tasty. Il propose des saveurs fraîches de bonbon à la fraise et fruit du dragon. Sa recette est composée d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG), pour un ratio de 50PG/50VG.

3. **Produit 3**
   - **id_produit**: 844
   - **Détails**: Le Fraise Candy est un e-liquide 50ml d'origine française, fabriqué par Prestige Fruits pour la gamme Sweety Fruits. Il propose une saveur fraîche de fraise façon bonbon, avec un ratio de 50PG/

In [121]:
id_produit_retourne = [464, 797, 844, 921]

In [120]:
retriever.invoke(query)

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 853, 'id_produit': 855, 'saveur': 'parfait, pomme, bonbon, bonbons'}, page_content="Le e-liquide Pomme Candy reprend tout ce qu'on attend d'ungoût bonbon: un fruit particulièrement alléchant, mais également juteux, frais et un peu acidulé, et une base de friandise ultra gourmande et sucrée ! Minutieusement préparé par Prestige Fruits, en France, ce e liquide est disponible en versionnon nicotinée et surboostée de 50ml. Sa fiole 60ml pourra accueillir un booster de nicotine (non inclus). Un bonbon à la pomme, juste comme on l'aime Vous aimez quand la vape est puissante et sucrée ? Il vous faut donc vous tourner en priorité vers les saveurs bonbons frais et fruités ! Ici, le fabricant français Prestige Fruits vous propose un mix depommestrès intéressant. En plus des notes typiques de ces fruits du verger, Prestige Fruits ajoute une bonne dose d'acidité et de sucre, pour une tendancefriandisebien assumée... Un 

In [122]:
best_id = [464, 797, 844, 921]

In [123]:
# Calculer la précision
def calculate_precision(recommended_ids, relevant_ids):
    # Nombre de recommandations pertinentes
    relevant_recommendations = set(recommended_ids).intersection(set(relevant_ids))
    precision = len(relevant_recommendations) / len(recommended_ids) if len(recommended_ids) > 0 else 0
    return precision

# Calculer la précision pour les recommandations données
precision = calculate_precision(id_produit_retourne, best_id)
print(f"Précision (Precision) : {precision * 100:.2f}%")

Précision (Precision) : 100.00%


il faut evaluer le rag , l'embedding est evaluer avec filter 

evaluation

In [181]:
from langchain.text_splitter import RecursiveCharacterTextSplitter

# Initialiser le découpeur de texte
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=2000,  # Taille des segments
    chunk_overlap=100,  # Chevauchement entre segments
    add_start_index=True,  # Ajouter un index de début
    separators=["\n\n", "\n", ".", " ", ""],  # Séparateurs de texte
)

In [182]:
lengths = [len(doc.page_content) for doc in documents]
print(f"Taille moyenne des documents : {sum(lengths) / len(lengths)} caractères")


Taille moyenne des documents : 3119.184846505552 caractères


In [186]:
# Découper les documents
docs_processed = text_splitter.split_documents(documents)

# Afficher un aperçu des segments découpés
for doc in docs_processed[:5]:  # Afficher les 5 premiers segments
    print(doc.page_content)
    print("-" * 50)

Le e-liquide Ragnarok par A&L Ultimate est un produitprêt à l'emploipour cigarette électronique. Dans sa fiole 10ml, vous retrouverez des saveurs de fruits rouges, accompagnées d'un goût frais de cassis. Idéal pour débuter, ce e-liquide vous est proposé en différents taux de nicotine au choix : 0, 3, 6, ou 12mg/ml. Qu'est-ce que le Ragnarok Ultimate ? Le Ragnarok, c'est unerecette fraiche aux goûts de fruitsdehaute qualité française, signée Arômes et Liquides (A&L). Ici, vous en profiterez dans sa version e-liquide prêt à vaper. Conforme à la loi TPD, le e liquide Ragnarok est présenté en fiole PET de 10ml. Pourquoi ? Afin de vous assurer unproduit déjà nicotiné à votre convenance! Pourquoi choisir le Ragnarok en e-liquide 10ml ? Simple, pratique et efficace, le e-liquide Ragnarok en 10ml permet de démarrer sans attendre votre séance de vapotage. Déjà minutieusement travaillé, dosé et nicotiné, il vous suffit de le verser dans votre réservoir de cigarette électronique pour l'utiliser !

In [187]:
print(f"Nombre de documents avant découpage : {len(documents)}")
print(f"Nombre de documents après découpage : {len(docs_processed)}")


Nombre de documents avant découpage : 1531
Nombre de documents après découpage : 3097


In [188]:
docs_processed

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 0, 'id_produit': 1, 'saveur': 'cassis, lime, fruits rouges, parfait', 'pg_vg': '50/50', 'origine': 'France', 'frais': 'Oui', 'surbooste': 'Non', 'brand': 'Arômes et Liquides (A&L)', 'gout': 'fruit', 'start_index': 0}, page_content="Le e-liquide Ragnarok par A&L Ultimate est un produitprêt à l'emploipour cigarette électronique. Dans sa fiole 10ml, vous retrouverez des saveurs de fruits rouges, accompagnées d'un goût frais de cassis. Idéal pour débuter, ce e-liquide vous est proposé en différents taux de nicotine au choix : 0, 3, 6, ou 12mg/ml. Qu'est-ce que le Ragnarok Ultimate ? Le Ragnarok, c'est unerecette fraiche aux goûts de fruitsdehaute qualité française, signée Arômes et Liquides (A&L). Ici, vous en profiterez dans sa version e-liquide prêt à vaper. Conforme à la loi TPD, le e liquide Ragnarok est présenté en fiole PET de 10ml. Pourquoi ? Afin de vous assurer unproduit déjà nicotiné à votre convenance

In [189]:
unique_products = {}
filtered_docs_processed = []

for doc in docs_processed:
    id_produit = doc.metadata['id_produit']
    if id_produit not in unique_products:
        unique_products[id_produit] = True
        filtered_docs_processed.append(doc)

filtered_docs_processed

[Document(metadata={'source': '../../RGBD/table_produits/produits.csv', 'row': 0, 'id_produit': 1, 'saveur': 'cassis, lime, fruits rouges, parfait', 'pg_vg': '50/50', 'origine': 'France', 'frais': 'Oui', 'surbooste': 'Non', 'brand': 'Arômes et Liquides (A&L)', 'gout': 'fruit', 'start_index': 0}, page_content="Le e-liquide Ragnarok par A&L Ultimate est un produitprêt à l'emploipour cigarette électronique. Dans sa fiole 10ml, vous retrouverez des saveurs de fruits rouges, accompagnées d'un goût frais de cassis. Idéal pour débuter, ce e-liquide vous est proposé en différents taux de nicotine au choix : 0, 3, 6, ou 12mg/ml. Qu'est-ce que le Ragnarok Ultimate ? Le Ragnarok, c'est unerecette fraiche aux goûts de fruitsdehaute qualité française, signée Arômes et Liquides (A&L). Ici, vous en profiterez dans sa version e-liquide prêt à vaper. Conforme à la loi TPD, le e liquide Ragnarok est présenté en fiole PET de 10ml. Pourquoi ? Afin de vous assurer unproduit déjà nicotiné à votre convenance

In [190]:
docs_processed = docs_processed[:200]  # Limiter à 100 documents
print(f"Nombre de documents après découpage : {len(docs_processed)}")


Nombre de documents après découpage : 200


In [191]:
print(f"Nombre de documents avant découpage : {len(documents)}")
print(f"Nombre de documents après découpage : {len(docs_processed)}")


Nombre de documents avant découpage : 1531
Nombre de documents après découpage : 200


1.2. Setup agents for question generation
We use Mixtral for QA couple generation because it it has excellent performance in leaderboards such as Chatbot Arena.

In [192]:
from huggingface_hub import InferenceClient
import json

repo_id = "mistralai/Mixtral-8x7B-Instruct-v0.1"

llm_client = InferenceClient(
    model=repo_id,
    timeout=120,
)


def call_llm(inference_client: InferenceClient, prompt: str):
    response = inference_client.post(
        json={
            "inputs": prompt,
            "parameters": {"max_new_tokens": 1000},
            "task": "text-generation",
        },
    )
    return json.loads(response.decode())[0]["generated_text"]


call_llm(llm_client, "This is a test context")

'This is a test context\n\n# Testing\n\n## Testing\n\nTesting is a crucial part of the development process. It ensures that the code is working as expected and helps to identify any bugs or issues early on.\n\nThere are different types of testing, including unit testing, integration testing, and end-to-end testing.\n\nUnit testing involves testing individual units of code, such as functions or methods, in isolation. This helps to ensure that each unit is working correctly and can be used as a building block for the rest of the application.\n\nIntegration testing involves testing how different units of code work together. This helps to ensure that the different parts of the application are communicating and working together correctly.\n\nEnd-to-end testing involves testing the entire application from start to finish. This helps to ensure that the application is working as expected and provides a good user experience.\n\nTesting can be done manually or automatically. Manual testing invol

In [193]:
QA_generation_prompt = """
Votre tâche est de rédiger une question factuelle et une réponse à partir d'un contexte concernant un produit e-liquide.
Votre question factuelle doit pouvoir être répondue par un renseignement factuel précis et concis tiré du contexte.
Votre question factuelle doit être formulée de la même manière que les questions qu'un utilisateur pourrait poser dans un moteur de recherche.
Cela signifie que votre question factuelle NE DOIT PAS mentionner des termes comme "selon le passage" ou "contexte".

Veuillez fournir votre réponse de la manière suivante :

Sortie:::
Question factuelle : (votre question factuelle sur le produit e-liquide)
Réponse : (votre réponse à la question factuelle)

Voici maintenant le contexte.

Contexte : {context}\n
Sortie:::"""


In [231]:
import random
from tqdm import tqdm

N_GENERATIONS = 100  # We intentionally generate only 10 QA couples here for cost and time considerations

print(f"Generating {N_GENERATIONS} QA couples...")
outputs = []
MAX_ANSWER_LENGTH = 300  # Limite de la longueur de la réponse

for sampled_context in tqdm(random.sample(docs_processed, N_GENERATIONS)):
    # Génération d'un couple QA
    output_QA_couple = call_llm(llm_client, QA_generation_prompt.format(context=sampled_context.page_content))
    try:
        question = output_QA_couple.split("Factoid question: ")[-1].split("Answer: ")[0]
        answer = output_QA_couple.split("Answer: ")[-1]
        
        # Limite la longueur de la réponse à 300 caractères
        if len(answer) > MAX_ANSWER_LENGTH:
            answer = answer[:MAX_ANSWER_LENGTH]  # Tronque la réponse si elle est trop longue
        
        outputs.append(
            {
                "context": sampled_context.page_content,
                "question": question,
                "answer": answer,
                "source_doc": sampled_context.metadata["source"],
            }
        )
    except Exception as e:
        print(f"Error processing context: {sampled_context.page_content}")
        print(f"Error: {e}")
        continue  # Continue si une erreur survient

# Vérifiez si 'outputs' contient plusieurs éléments avant de créer le DataFrame
if outputs:
    # Création du DataFrame
    df = pd.DataFrame(outputs)
    print(f"Dataframe created with {len(df)} rows.")
else:
    print("No valid QA couples were generated.")


Generating 100 QA couples...


 30%|███       | 30/100 [00:11<00:26,  2.69it/s]


HfHubHTTPError: 402 Client Error: Payment Required for url: https://api-inference.huggingface.co/models/mistralai/Mixtral-8x7B-Instruct-v0.1 (Request ID: Root=1-67c04aa5-7a0fa96b56d46af005154011;f7308492-84cb-4587-a40a-bfd15c202341)

You have exceeded your monthly included credits for Inference Providers. Subscribe to PRO to get 20x more monthly allowance.

In [ ]:
df.shape

(100, 4)

In [ ]:
df.head(1)

context  \
0  Le Mars 200ml est un e-liquide pour cigarette électronique fabriqué en France par Space Fruit à la saveur fraîche de fruits rouges et de grenade façon grenadine. Il est élaboré à partir d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG), pour un ratio50PG/50VG. Non nicotiné de base, il est surboosté en arômes, et vous permet donc de le booster au besoin sans perte de saveur. Pour réaliser vos mélanges, il faudra vous munir d'une flacon vide du volume de votre choix. Notez que cette fiole est dotée d'un bouchon avec protection enfant et d'un embout fin. Qui est Space Fruit ? Space Fruits est un fabricant français spécialisé dans la reproduction des saveurs de fruits et proposées dans des recettes à booster au format de 200ml ! Comment préparer votre e-liquide Mars ? Le Marsest proposé en version200mlboostée en arômes dans un flacon de200ml. Si vous le souhaitez, vous pouvez ajouter un ou plusieurs boosters de nicotine selon vos besoins sans perte de saveur. Pour booster votre e-liquide, vous devez : Indications pour préparer votre e-liquide surboosté de 50 ml : La place disponible dans le flacon d'origine n’est peut-être pas suffisante pour booster votre e-liquide au taux de nicotine souhaité. Pour les dosages importants, nous vous conseillons l’utilisation de contenants plus importants commeun flacon de 100ml graduéouun flacon Twist de 230ml gradué. Astuce : pensez à adapter votre matériel au ratio PG/VG de votre e-liquide ! Vous limiterez ainsi le risque de fuite et l’usure prématurée de vos résistances ! Quel taux de nicotine choisir pour votre e-liquide ? Le choix de votre taux de nicotine dépend de votre profil de fumeur ainsi que de la cigarette électronique utilisée : Si vous utilisez du matériel plus performant avec une résistance inférieure à 1 ohm et pour une puissance supérieure à 30 watts, vous pouvez diviser votre taux de nicotine par deux   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [ ]:
# Remplacer les \n par un espace ou une chaîne vide
df['question'] = df['question'].str.replace('\n', ' ', regex=False)
df.head(1)

context  \
0  Le Mars 200ml est un e-liquide pour cigarette électronique fabriqué en France par Space Fruit à la saveur fraîche de fruits rouges et de grenade façon grenadine. Il est élaboré à partir d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG), pour un ratio50PG/50VG. Non nicotiné de base, il est surboosté en arômes, et vous permet donc de le booster au besoin sans perte de saveur. Pour réaliser vos mélanges, il faudra vous munir d'une flacon vide du volume de votre choix. Notez que cette fiole est dotée d'un bouchon avec protection enfant et d'un embout fin. Qui est Space Fruit ? Space Fruits est un fabricant français spécialisé dans la reproduction des saveurs de fruits et proposées dans des recettes à booster au format de 200ml ! Comment préparer votre e-liquide Mars ? Le Marsest proposé en version200mlboostée en arômes dans un flacon de200ml. Si vous le souhaitez, vous pouvez ajouter un ou plusieurs boosters de nicotine selon vos besoins sans perte de saveur. Pour booster votre e-liquide, vous devez : Indications pour préparer votre e-liquide surboosté de 50 ml : La place disponible dans le flacon d'origine n’est peut-être pas suffisante pour booster votre e-liquide au taux de nicotine souhaité. Pour les dosages importants, nous vous conseillons l’utilisation de contenants plus importants commeun flacon de 100ml graduéouun flacon Twist de 230ml gradué. Astuce : pensez à adapter votre matériel au ratio PG/VG de votre e-liquide ! Vous limiterez ainsi le risque de fuite et l’usure prématurée de vos résistances ! Quel taux de nicotine choisir pour votre e-liquide ? Le choix de votre taux de nicotine dépend de votre profil de fumeur ainsi que de la cigarette électronique utilisée : Si vous utilisez du matériel plus performant avec une résistance inférieure à 1 ohm et pour une puissance supérieure à 30 watts, vous pouvez diviser votre taux de nicotine par deux   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [ ]:
# Fonction pour extraire le texte entre la deuxième occurrence de "Question factuelle :" et "Réponse :"
def extract_second_q_and_r(text):
    # Utilisation d'une expression régulière pour capturer le texte entre la deuxième Question factuelle et Réponse
    pattern = r"(?:Question factuelle :.*?)(Question factuelle :.*?)(Réponse :.*?)(?=Question factuelle :|$)"
    match = re.search(pattern, text, re.DOTALL)
    if match:
        return match.group(1).replace('Question factuelle :', '').replace('Réponse :', '').strip()
    else:
        return None

# Appliquer la fonction pour créer une nouvelle colonne 'Q'
df['Q'] = df['question'].apply(extract_second_q_and_r)

df.head(1)

context  \
0  Le Mars 200ml est un e-liquide pour cigarette électronique fabriqué en France par Space Fruit à la saveur fraîche de fruits rouges et de grenade façon grenadine. Il est élaboré à partir d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG), pour un ratio50PG/50VG. Non nicotiné de base, il est surboosté en arômes, et vous permet donc de le booster au besoin sans perte de saveur. Pour réaliser vos mélanges, il faudra vous munir d'une flacon vide du volume de votre choix. Notez que cette fiole est dotée d'un bouchon avec protection enfant et d'un embout fin. Qui est Space Fruit ? Space Fruits est un fabricant français spécialisé dans la reproduction des saveurs de fruits et proposées dans des recettes à booster au format de 200ml ! Comment préparer votre e-liquide Mars ? Le Marsest proposé en version200mlboostée en arômes dans un flacon de200ml. Si vous le souhaitez, vous pouvez ajouter un ou plusieurs boosters de nicotine selon vos besoins sans perte de saveur. Pour booster votre e-liquide, vous devez : Indications pour préparer votre e-liquide surboosté de 50 ml : La place disponible dans le flacon d'origine n’est peut-être pas suffisante pour booster votre e-liquide au taux de nicotine souhaité. Pour les dosages importants, nous vous conseillons l’utilisation de contenants plus importants commeun flacon de 100ml graduéouun flacon Twist de 230ml gradué. Astuce : pensez à adapter votre matériel au ratio PG/VG de votre e-liquide ! Vous limiterez ainsi le risque de fuite et l’usure prématurée de vos résistances ! Quel taux de nicotine choisir pour votre e-liquide ? Le choix de votre taux de nicotine dépend de votre profil de fumeur ainsi que de la cigarette électronique utilisée : Si vous utilisez du matériel plus performant avec une résistance inférieure à 1 ohm et pour une puissance supérieure à 30 watts, vous pouvez diviser votre taux de nicotine par deux   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [227]:

df['A'] = df['question'].str.split(r'\nRéponse :').str[2]
df.head(6)

context  \
0                                                                                            Le Mars 200ml est un e-liquide pour cigarette électronique fabriqué en France par Space Fruit à la saveur fraîche de fruits rouges et de grenade façon grenadine. Il est élaboré à partir d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG), pour un ratio50PG/50VG. Non nicotiné de base, il est surboosté en arômes, et vous permet donc de le booster au besoin sans perte de saveur. Pour réaliser vos mélanges, il faudra vous munir d'une flacon vide du volume de votre choix. Notez que cette fiole est dotée d'un bouchon avec protection enfant et d'un embout fin. Qui est Space Fruit ? Space Fruits est un fabricant français spécialisé dans la reproduction des saveurs de fruits et proposées dans des recettes à booster au format de 200ml ! Comment préparer votre e-liquide Mars ? Le Marsest proposé en version200mlboostée en arômes dans un flacon de200ml. Si vous le souhaitez, vous pouvez ajouter un ou plusieurs boosters de nicotine selon vos besoins sans perte de saveur. Pour booster votre e-liquide, vous devez : Indications pour préparer votre e-liquide surboosté de 50 ml : La place disponible dans le flacon d'origine n’est peut-être pas suffisante pour booster votre e-liquide au taux de nicotine souhaité. Pour les dosages importants, nous vous conseillons l’utilisation de contenants plus importants commeun flacon de 100ml graduéouun flacon Twist de 230ml gradué. Astuce : pensez à adapter votre matériel au ratio PG/VG de votre e-liquide ! Vous limiterez ainsi le risque de fuite et l’usure prématurée de vos résistances ! Quel taux de nicotine choisir pour votre e-liquide ? Le choix de votre taux de nicotine dépend de votre profil de fumeur ainsi que de la cigarette électronique utilisée : Si vous utilisez du matériel plus performant avec une résistance inférieure à 1 ohm et pour une puissance supérieure à 30 watts, vous pouvez diviser votre taux de nicotine par deux   
1  Cete-liquide fruitéet fabriqué en France vous propose un mix de kiwi, goyave, fruit du dragon et fraise, dans une formule prête à l'emploi imaginée par Swoke. Sélectionnez à la commande le taux en nicotine qui vous convient :0, 3, 6 ou 12mg/ml. Le Pixel est fabriqué en France à partir de propylène glycol (PG), de glycérine végétale (VG), et d'arômes alimentaires avec une base 50PG/50VG. Cet e-liquide est livré fans un flacon souple de type PET de 10ml équipé d'un bouchon avec sécurité enfant et d'un embout fin pour remplir facilement toutes vos cigarettes électroniques. Qui est Swoke ? Le fabricant français Swoke doit son succès dans le monde de la vape grâce à ses nombreuses gammes à thèmes de e-liquides et concentrés DIY finement réalisés, comme par exemple Saint Flava ou encore Vape Party. Nos conseils pour utiliser votre e-liquide Pixel L'utilisation d'un e-liquide est exclusivement réservée à la cigarette électronique. Nous vous recommandons de bien agiter votre flacon de e-liquide avant emploi. Pour limiter les risques de fuites et prolonger la durée de vie de vos résistances, nous vous conseillons d'utiliser un clearomiseur adapté au taux PG/VG de votre e-liquide. Quel taux de nicotine choisir pour votre e-liquide ? Le choix de votre taux de nicotine dépend de votre profil de fumeur ainsi que de la cigarette électronique utilisée. Si vous utilisez une cigarette électronique équipée d'une résistance égale ou supérieure à 1 ohm et à une puissance ne dépassant pas les 30 watts, voici nos recommandations pour choisir votre taux de nicotine : Si vous utilisez une cigarette électronique plus performante équipée de résistances dont la valeur est inférieure à 1 ohm et pour une puissance supérieure à 30 watts, nous vous conseillons d'utiliser un taux de nicotine plus faible : Conservation de votre e-liquide Pour une conservation optimale de votre e-liquide, nous vous conseillons de stocker votre flacon à l'abri de la lumière dans un droit sec et à

In [221]:
df.isna().sum()

context        0
question       0
answer         0
source_doc     0
Q             11
A             11
dtype: int64

In [224]:
nan_rows = df[df['Q'].isna()]
nan_rows

context  \
9                                                                                                                            . Si vous utilisez une cigarette électronique équipée d'une résistance égale ou supérieure à 1ohm et à une puissance ne dépassant pas les 30 watts, voici nos recommandations pour choisir votre taux de nicotine : Si vous utilisez une cigarette électronique plus performante équipée de résistances dont la valeur est inférieure à 1 ohm et pour une puissance supérieure à 30 watts, nous vous conseillons d'utiliser un taux de nicotine plus faible : À qui s'adresse ce e-liquide 10ml ? Avec un tel format prêt à l'emploi, le e-liquide Ragnarok Ultimate se veut particulièrement adapté aux vapoteurs débutants ! Non seulement il sera très facile à utiliser, mais il vous permettra de mieux comprendre et gérer votre taux nicotinique. Quant à son mélange de fruits rouges et de fraicheur, il estspécialement fait pour s'adapter à différents types de vapoteur. De quoi se compose le Ragnarok Ultimate ? Comme tout e-liquide pour cigarette électronique, le Ragnarok se compose d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG). Tous ces ingrédients sont minutieusement sélectionnés par Arômes et Liquides. Chez nous, ce qui compte, c'est la qualité ! Si la recette du Ragnarok Ultimate est aussi reconnue, c'est bien grâce à cela : avec des composants de premier choix et une fabrication comme un conditionnement100% français, ce e-liquide ne peut être que de qualité premium ! Afin d'équilibrer la recette ainsi que le hit en gorge, A&L propose son e liquide Ultimate Ragnarok en50PG/50VG. Enfin, pour rester conforme à la loi TPD et vous présenter un e-liquide nicotiné, A&L choisit un conditionnement en fioles PET de 10ml, munies de bouchons sécurisés (protections enfant) et d'embouts fins compte-gouttes. N.B : Vous ne trouverez aucune trace de diacétyle dans les produits A&L. De même, aucun test sur des animaux n'est pratiqué chez nous   
10                                               Le Mistyk est un e-liquide à booster au format 50ml de la collection Juice Heroes par Liquideo. Il vous propose dessaveurs fraîches de pitayadans sa recette fabriquée en France. Composé d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG), dans un ratio 30PG/70VG, vous pouvez au besoin ajouter des boosters 10ml de nicotine (vendus séparément). Il vous est livré dans une fiole de 70ml dotée d'un bouchon sécurisé et d'un embout fin simplifiant le remplissage de votre réservoir. Qui est Liquideo ? Liquideo est un fabricant français, et plus précisément parisien, spécialisé dans la création d'e-liquides. Se destinant à tous les vapoteurs, ses recettes se déclinent sous plusieurs gammes dont Multi Freeze ou encore Evolution, pour ne citer que celles-ci. Comment préparer votre e-liquide Mistyk ? Le Mistyk est proposé en version50mlboostée en arômes dans un flacon de70ml. Si vous le souhaitez, vous pouvez ainsi ajouter un ou plusieurs boosters de nicotine selon vos besoins sans perte de saveur. Pour booster votre e-liquide, vous devez : Indications pour préparer votre e-liquide surboosté de 50 ml : La place disponible dans le flacon d'origine n’est peut-être pas suffisante pour booster votre e-liquide au taux de nicotine souhaité. Pour les dosages importants, nous vous conseillons l’utilisation de contenants plus importants commeun flacon de 100ml graduéouun flacon Twist de 230ml gradué. Astuce : pensez à adapter votre matériel au ratio PG/VG de votre e-liquide ! Vous limiterez ainsi le risque de fuite et l’usure prématurée de vos résistances ! Quel taux de nicotine choisir pour votre e-liquide ? Le choix de votre taux de nicotine dépend de votre profil de fumeur ainsi que de la cigarette électronique utilisée : Si vous utilisez du matériel plus performant avec une résistance inférieure à 1 ohm et pour une puissance supérieure à 30 watts, vous pouvez diviser votre taux de nicotine par deux   
20 

In [162]:
# Garder seulement les colonnes 'context', 'Q' et 'R'
df = df[['context', 'Q', 'R']]
# Renommer les colonnes pour plus de clarté
df = df.rename(columns={'Q': 'question', 'R': 'answer'})
df.head(1)

context  \
0  . Si vous utilisez une cigarette électronique équipée d'une résistance égale ou supérieure à 1 ohm et à une puissance ne dépassant pas les 30 watts, voici nos recommandations pour choisir votre taux de nicotine : Si vous utilisez une cigarette électronique plus performante équipée de résistances dont la valeur est inférieure à 1 ohm et pour une puissance supérieure à 30 watts, nous vous conseillons d'utiliser un taux de nicotine plus faible : Conservation de votre e-liquide Pour une conservation optimale de votre e-liquide, nous vous conseillons de stocker votre flacon à l'abri de la lumière dans un droit sec et à température ambiante. Après contacts répétés à l'air et à la lumière, la couleur de votre e-liquide peut se foncer. Ce changement de couleur n'affecte ni la qualité ni le goût de votre e-liquide. La date indiquée sur l'étiquette est une DLUO (date limite d'utilisation optimale) ou DDM (date de durabilité minimale). Passé cette date, le e-liquide peut encore être consommé. Mises en garde et contre-indications : Précautions d'emploi :   

                                                             question  \
0   Quelle est la date limite d'utilisation optimale d'un e-liquide ?   

                                                                                                                                                                                                                                           answer  
0  La date limite d'utilisation optimale d'un e-liquide est indiquée sur l'étiquette et correspond à la DLUO (date limite d'utilisation optimale) ou DDM (date de durabilité minimale). Passé cette date, le e-liquide peut encore être consommé.

df to documents 

In [164]:
df = df[:10]
df.shape

(10, 3)

1.3. Setup critique agents
- quality check
-build critique agents that  will rate each question on several criteria, given in this paper
    - Groundedness: can the question be answered from the given context?
    - Relevance: is the question relevant to users? For instance, "What is the date when transformers 4.29.1 was released?" is not relevant for ML practitioners.

In [170]:
question_groundedness_critique_prompt = """
Vous allez recevoir un contexte et une question.
Votre tâche est de fournir une "note totale" évaluant dans quelle mesure la question peut être répondue de manière claire et sans ambiguïté avec le contexte fourni.
Évaluez votre réponse sur une échelle de 1 à 5, où 1 signifie que la question ne peut pas du tout être répondue avec le contexte donné, et 5 signifie que la question peut être clairement et sans ambiguïté répondue avec le contexte.

Fournissez votre réponse comme suit :

Réponse:::
Évaluation : (votre raisonnement pour la note, sous forme de texte)
Note totale : (votre note, un nombre entre 1 et 5)

Vous DEVEZ fournir des valeurs pour 'Évaluation :' et 'Note totale :' dans votre réponse.

Voici maintenant la question et le contexte.

Question : {question}\n
Contexte : {context}\n
Réponse:::  """

question_relevance_critique_prompt = """
Vous allez recevoir une question.
Votre tâche est de fournir une "note totale" représentant l'utilité de cette question pour les développeurs de machine learning travaillant sur des applications NLP avec l'écosystème Hugging Face.
Évaluez votre réponse sur une échelle de 1 à 5, où 1 signifie que la question n'est pas du tout utile, et 5 signifie que la question est extrêmement utile.

Fournissez votre réponse comme suit :

Réponse:::
Évaluation : (votre raisonnement pour la note, sous forme de texte)
Note totale : (votre note, un nombre entre 1 et 5)

Vous DEVEZ fournir des valeurs pour 'Évaluation :' et 'Note totale :' dans votre réponse.

Voici maintenant la question.

Question : {question}\n
Réponse::: """

question_standalone_critique_prompt = """
Vous allez recevoir une question.
Votre tâche est de fournir une "note totale" représentant dans quelle mesure cette question est indépendante du contexte.
Évaluez votre réponse sur une échelle de 1 à 5, où 1 signifie que la question dépend d'informations supplémentaires pour être comprise, et 5 signifie que la question a un sens par elle-même.
Par exemple, si la question fait référence à un contexte particulier, comme "dans le contexte" ou "dans le document", la note doit être de 1.
Les questions peuvent contenir des termes techniques obscurs ou des acronymes comme Gradio, Hub, Hugging Face ou Space et recevoir tout de même une note de 5 : il suffit que l'opérateur avec accès à la documentation puisse comprendre de quoi il s'agit.

Par exemple, la question "Quel est le taux de nicotine recommandé pour une cigarette électronique équipée d'une résistance inférieure à 1 ohm et d'une puissance supérieure à 30 watts ?" devrait recevoir une note de 1, car elle fait référence explicitement à un contexte précis (le type de cigarette électronique), et donc la question n'est pas indépendante du contexte.

Fournissez votre réponse comme suit :

Réponse:::
Évaluation : (votre raisonnement pour la note, sous forme de texte)
Note totale : (votre note, un nombre entre 1 et 5)

Vous DEVEZ fournir des valeurs pour 'Évaluation :' et 'Note totale :' dans votre réponse.

Voici maintenant la question.

Question : {question}\n
Réponse::: """

In [171]:
# Liste pour stocker les résultats
outputs = []

# Boucle pour traiter chaque ligne du DataFrame
print("Generating critique for each QA couple...")
for _, row in tqdm(df.iterrows(), total=df.shape[0]):
    context = row['context']
    question = row['question']
    answer = row['answer']
    
    # Créer un document structuré avec context, question, et answer
    output = {
        "context": context,
        "question": question,
        "answer": answer
    }
    
    # Générer les critiques
    evaluations = {
        "groundedness": call_llm(
            llm_client,
            question_groundedness_critique_prompt.format(context=output["context"], question=output["question"]),
        ),
        "relevance": call_llm(
            llm_client,
            question_relevance_critique_prompt.format(question=output["question"]),
        ),
        "standalone": call_llm(
            llm_client,
            question_standalone_critique_prompt.format(question=output["question"]),
        ),
    }
    
    # Extraire les scores et évaluations
    try:
        for criterion, evaluation in evaluations.items():
            score, eval = (
                int(evaluation.split("Total rating: ")[-1].strip()),  # Score
                evaluation.split("Total rating: ")[-2].split("Evaluation: ")[1],  # Evaluation
            )
            output.update(
                {
                    f"{criterion}_score": score,
                    f"{criterion}_eval": eval,
                }
            )
        outputs.append(output)
    except Exception as e:
        print(f"Error evaluating {question}: {e}")
        continue  # Passer à la génération suivante en cas d'erreur

# Créer un DataFrame avec les critiques
df_with_critique = pd.DataFrame(outputs)

Generating critique for each QA couple...


 10%|█         | 1/10 [00:54<08:08, 54.23s/it]

Error evaluating  Quelle est la date limite d'utilisation optimale d'un e-liquide ?: invalid literal for int() with base 10: 'Vous allez recevoir un contexte et une question.\nVotre tâche est de fournir une "note totale" évaluant dans quelle mesure la question peut être répondue de manière claire et sans ambiguïté avec le c


 20%|██        | 2/10 [01:17<04:47, 35.92s/it]

Error evaluating  De quoi se compose le e-liquide Valkyrie 50ml d'A&L ?: invalid literal for int() with base 10: 'Vous allez recevoir un contexte et une question.\nVotre tâche est de fournir une "note totale" évaluant dans quelle mesure la question peut être répondue de manière claire et sans ambiguïté avec le c


...

Error evaluating  Comment préparer un e-liquide surboosté de 100 ml de Pomme Cerise Bubble Gum ?: invalid literal for int() with base 10: 'Vous allez recevoir un contexte et une question.\nVotre tâche est de fournir une "note totale" évaluant dans quelle mesure la question peut être répondue de manière claire et sans ambiguïté avec le c


 90%|█████████ | 9/10 [02:24<00:12, 12.36s/it]

Error evaluating nan: invalid literal for int() with base 10: 'Vous allez recevoir un contexte et une question.\nVotre tâche est de fournir une "note totale" évaluant dans quelle mesure la question peut être répondue de manière claire et sans ambiguïté avec le c


100%|██████████| 10/10 [02:47<00:00, 16.79s/it]

Error evaluating  Quel est le ratio PG/VG du e-liquide Pomme Verte par A&L ?: invalid literal for int() with base 10: 'Vous allez recevoir un contexte et une question.\nVotre tâche est de fournir une "note totale" évaluant dans quelle mesure la question peut être répondue de manière claire et sans ambiguïté avec le c


In [174]:
df_with_critique

Empty DataFrame
Columns: []
Index: []

In [161]:
# Ajouter les critiques pour chaque QA
print("Generating critique for each QA couple...")
for output in tqdm(outputs):
    evaluations = {
        "groundedness": call_llm(
            llm_client,
            question_groundedness_critique_prompt.format(context=output["context"], question=output["question"]),
        ),
        "relevance": call_llm(
            llm_client,
            question_relevance_critique_prompt.format(question=output["question"]),
        ),
        "standalone": call_llm(
            llm_client,
            question_standalone_critique_prompt.format(question=output["question"]),
        ),
    }
    
    try:
        # Extraire les scores et évaluations
        for criterion, evaluation in evaluations.items():
            score, eval = (
                int(evaluation.split("Total rating: ")[-1].strip()),  # Score
                evaluation.split("Total rating: ")[-2].split("Evaluation: ")[1],  # Evaluation
            )
            output.update(
                {
                    f"{criterion}_score": score,
                    f"{criterion}_eval": eval,
                }
            )
    except Exception as e:
        print(f"Error evaluating {output['question']}: {e}")
        continue  # Passer à la génération suivante en cas d'erreur

# Créer un DataFrame avec les critiques
df_with_critique = pd.DataFrame(outputs)

Generating critique for each QA couple...


  8%|▊         | 8/100 [01:02<17:00, 11.09s/it]

Error evaluating 
Votre tâche est de rédiger une question factuelle et une réponse à partir d'un contexte concernant un produit e-liquide.
Votre question factuelle doit pouvoir être répondue par un renseignement factuel précis et concis tiré du contexte.
Votre question factuelle doit être formulée de la même manière que les questions qu'un utilisateur pourrait poser dans un moteur de recherche.
Cela signifie que votre question factuelle NE DOIT PAS mentionner des termes comme "selon le passage" ou "contexte".

Veuillez fournir votre réponse de la manière suivante :

Sortie:::
Question factuelle : (votre question factuelle sur le produit e-liquide)
Réponse : (votre réponse à la question factuelle)

Voici maintenant le contexte.

Contexte : Fabriqué en France par Secret's Lab, le e-liquide pour cigarette électronique Pomme Cerise Bubble Gum est issu de la collection Biggy Bear. Composé d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG), il vous est proposé dans

 23%|██▎       | 23/100 [02:26<08:11,  6.39s/it]

Error evaluating 
Votre tâche est de rédiger une question factuelle et une réponse à partir d'un contexte concernant un produit e-liquide.
Votre question factuelle doit pouvoir être répondue par un renseignement factuel précis et concis tiré du contexte.
Votre question factuelle doit être formulée de la même manière que les questions qu'un utilisateur pourrait poser dans un moteur de recherche.
Cela signifie que votre question factuelle NE DOIT PAS mentionner des termes comme "selon le passage" ou "contexte".

Veuillez fournir votre réponse de la manière suivante :

Sortie:::
Question factuelle : (votre question factuelle sur le produit e-liquide)
Réponse : (votre réponse à la question factuelle)

Voici maintenant le contexte.

Contexte : . Ici, le Ragnarok Zero est uniquement proposé en fiole de type PET 60ml. Non nicotiné, il contient 50ml de e-liquide en 0mg. Son flacon dévoilera un bouchon sécurisé (protection enfant) et un embout fin très pratique.

Sortie:::
Question factuelle : 

...

Error evaluating 
Votre tâche est de rédiger une question factuelle et une réponse à partir d'un contexte concernant un produit e-liquide.
Votre question factuelle doit pouvoir être répondue par un renseignement factuel précis et concis tiré du contexte.
Votre question factuelle doit être formulée de la même manière que les questions qu'un utilisateur pourrait poser dans un moteur de recherche.
Cela signifie que votre question factuelle NE DOIT PAS mentionner des termes comme "selon le passage" ou "contexte".

Veuillez fournir votre réponse de la manière suivante :

Sortie:::
Question factuelle : (votre question factuelle sur le produit e-liquide)
Réponse : (votre réponse à la question factuelle)

Voici maintenant le contexte.

Contexte : . Nos conseils pour la maturation de votre e-liquide surboosté De la même façon que pour un e-liquide DIY, on peut observer un temps de repos avec un e-liquide surboosté en arômes après l’ajout d’un ou plusieurs boosters de nicotine. Ce temps de matur

 30%|███       | 30/100 [03:16<05:03,  4.33s/it]

Error evaluating 
Votre tâche est de rédiger une question factuelle et une réponse à partir d'un contexte concernant un produit e-liquide.
Votre question factuelle doit pouvoir être répondue par un renseignement factuel précis et concis tiré du contexte.
Votre question factuelle doit être formulée de la même manière que les questions qu'un utilisateur pourrait poser dans un moteur de recherche.
Cela signifie que votre question factuelle NE DOIT PAS mentionner des termes comme "selon le passage" ou "contexte".

Veuillez fournir votre réponse de la manière suivante :

Sortie:::
Question factuelle : (votre question factuelle sur le produit e-liquide)
Réponse : (votre réponse à la question factuelle)

Voici maintenant le contexte.

Contexte : . Nos conseils pour la maturation de votre e-liquide surboosté De la même façon que pour un e-liquide DIY, on peut observer un temps de repos avec un e-liquide surboosté en arômes après l’ajout d’un ou plusieurs boosters de nicotine. Ce temps de matur

 30%|███       | 30/100 [03:50<08:57,  7.68s/it]


KeyboardInterrupt: 

In [94]:
df_with_critique

context  \
0  Le Acai Fruit Pot 100ml est un e-liquide à boo...   
1  . Nos conseils pour la maturation de votre e-l...   
2  . Nos conseils pour la maturation de votre e-l...   
3  Le Forest Fruits 100ml est un e-liquide à boos...   
4  . Pour bien l'utiliser, suivez les conseils de...   
5  Le Oni Ultimate 10ml est un e-liquide pour cig...   
6  . Astuce : pensez à adapter votre matériel au ...   
7  . Si vous utilisez une cigarette électronique ...   
8  Le Red Astaire 50ml est un e-liquide pour ciga...   
9  Ce e-liquide pour cigarette électronique augoû...   

                                            question  \
0  (votre question factuelle sur le produit e-liq...   
1  (votre question factuelle sur le produit e-liq...   
2  (votre question factuelle sur le produit e-liq...   
3  (votre question factuelle sur le produit e-liq...   
4  (votre question factuelle sur le produit e-liq...   
5  (votre question factuelle sur le produit e-liq...   
6  (votre question factuelle sur le produit e-liq...   
7  (votre question factuelle sur le produit e-liq...   
8  (votre question factuelle sur le produit e-liq...   
9  (votre question factuelle sur le produit e-liq...   

                                              answer  \
0  (votre réponse à la question factuelle)\n\nVoi...   
1  (votre réponse à la question factuelle)\n\nVoi...   
2  (votre réponse à la question factuelle)\n\nVoi...   
3  (votre réponse à la question factuelle)\n\nVoi...   
4  (votre réponse à la question factuelle)\n\nVoi...   
5  (votre réponse à la question factuelle)\n\nVoi...   
6  (votre réponse à la question factuelle)\n\nVoi...   
7  (votre réponse à la question factuelle)\n\nVoi...   
8  (votre réponse à la question factuelle)\n\nVoi...   
9  (votre réponse à la question factuelle)\n\nVoi...   

                               source_doc  groundedness_score  \
0  ../../RGBD/table_produits/produits.csv                 1.0   
1  ../../RGBD/table_produits/produits.csv                 1.0   
2  ../../RGBD/table_produits/produits.csv                 1.0   
3  ../../RGBD/table_produits/produits.csv                 1.0   
4  ../../RGBD/table_produits/produits.csv                 NaN   
5  ../../RGBD/table_produits/produits.csv                 5.0   
6  ../../RGBD/table_produits/produits.csv                 5.0   
7  ../../RGBD/table_produits/produits.csv                 1.0   
8  ../../RGBD/table_produits/produits.csv                 1.0   
9  ../../RGBD/table_produits/produits.csv                 1.0   

                                   groundedness_eval  relevance_score  \
0  The context provides a detailed description of...              1.0   
1  The question asks about the taste of the e-liq...              1.0   
2  The question asks about the taste of the e-liq...              1.0   
3  The context provides information about the e-l...              1.0   
4                                                NaN              NaN   
5  The context provides a clear and unambiguous a...              1.0   
6  The context provides clear instructions on how...              1.0   
7  The context provides information about the rec...              1.0   
8  The question asks about the taste of the e-liq...              1.0   
9  \nThe context does not provide any information...              1.0   

                                      relevance_eval  standalone_score  \
0  This question is not useful for machine learni...               5.0   
1  This question is not useful for machine learni...               5.0   
2  This question is not useful for machine learni...               5.0   
3  This question is not useful for machine learni...               5.0   
4                                                NaN               NaN   
5  This question is not useful for machine learni...               5.0   
6  This question is not useful for machine learni...               5.0   
7  This question is not useful for machine learni...               5.0   
8  This 

In [103]:
df.to_csv("df_critique.csv")

In [ ]:
pd.set_option("display.max_colwidth", None)

In [95]:
pd.set_option("display.max_colwidth", None)

In [96]:
print("Evaluation dataset before filtering:")
display(
    df_with_critique[
        [
            "question",
            "answer",
            "groundedness_score",
            "relevance_score",
            "standalone_score",
        ]
    ]
)

Evaluation dataset before filtering:


question  \
0  (votre question factuelle sur le produit e-liquide)   
1  (votre question factuelle sur le produit e-liquide)   
2  (votre question factuelle sur le produit e-liquide)   
3  (votre question factuelle sur le produit e-liquide)   
4  (votre question factuelle sur le produit e-liquide)   
5  (votre question factuelle sur le produit e-liquide)   
6  (votre question factuelle sur le produit e-liquide)   
7  (votre question factuelle sur le produit e-liquide)   
8  (votre question factuelle sur le produit e-liquide)   
9  (votre question factuelle sur le produit e-liquide)   

                                                                                                                                                                                                                                                                                                             answer  \
0  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : Le Acai Fruit Pot 100ml est un e-liquide à booster issu de la collection Fruits de la marque Chuffed, auxsaveurs fraîches de kiwi, fraise et baie d'açaï. Sa recette fabriquée en France se compose d'arômes alimentaires   
1  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : . Nos conseils pour la maturation de votre e-liquide surboosté De la même façon que pour un e-liquide DIY, on peut observer un temps de repos avec un e-liquide surboosté en arômes après l’ajout d’un ou plusieurs boost   
2  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : . Nos conseils pour la maturation de votre e-liquide surboosté De la même façon que pour un e-liquide DIY, on peut observer un temps de repos avec un e-liquide surboosté en arômes après l’ajout d’un ou plusieurs boost   
3  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : Le Forest Fruits 100ml est un e-liquide à booster issu de la collection Fruits de la marque Chuffed, auxsaveurs de myrtilles, de fraises et de framboises. Sa recette fabriquée en France se compose d'arômes alimentaire   
4  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : . Pour bien l'utiliser, suivez les conseils des pandas d'A&L ! Sans nicotine Vous avez choisi le e-liquide Kami Ultimate en 50ml et souhaitez le vapotersans nicotine? Il vous suffira : Avec nicotine Vous avez encore b   
5  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : Le Oni Ultimate 10ml est un e-liquide pour cigarette électronique signé Arômes et Liquides (A&L). Il est proposé ici enversion prête à l'emploi. Vous pourrez donc l'utiliser de suite dans votre matériel ! Disponible e   
6  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : . Astuce : pensez à adapter votre matériel au ratio PG/VG de votre e-liquide ! Vous limiterez ainsi le risque de fuite et l’usure prématurée de vos résistances ! Quel taux de nicotine choisir pour votre e-liquide ? Le   
7  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : . Si vous utilisez une cigarette électronique équipée d'une résistance égale ou supérieure à 1 ohm et à une puissance ne dépassant pas les 30 watts, voici nos recommandations pour choisir votre taux de nicotine : Si v   
8  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : Le Red Astaire 50ml est un e-liquide pour cigarette électronique, au format à booster, fabriqué au Royaume-Uni par T-Juice. Il vous propose dessaveurs fraîches de fruits rouges, d'anis, de menthe et d'eucalyptus. Il e   
9  (votre réponse à la question factuelle)\n\nVoici maintenant le contexte.\n\nContexte : Ce e-liquide pour cigarette électronique augoût de pomme verteest fabriqué en France par Arômes et Liquides (A&L). Il est composé d'arômes alimentaires, de propylène glycol (PG) et de glycérine végétale (VG)

In [97]:
generated_questions = df_with_critique.loc[
    (df_with_critique["groundedness_score"] >= 4)
    & (df_with_critique["relevance_score"] >= 4)
    & (df_with_critique["standalone_score"] >= 4)
]
print("============================================")
print("Final evaluation dataset:")
display(
    generated_questions[
        [
            "question",
            "answer",
            "groundedness_score",
            "relevance_score",
            "standalone_score",
        ]
    ]
)

Final evaluation dataset:


Empty DataFrame
Columns: [question, answer, groundedness_score, relevance_score, standalone_score]
Index: []

In [100]:
from datasets import Dataset


In [101]:
eval_dataset = Dataset.from_pandas(generated_questions, split="train", preserve_index=False)

In [102]:
eval_dataset

Dataset({
    features: ['context', 'question', 'answer', 'source_doc', 'groundedness_score', 'groundedness_eval', 'relevance_score', 'relevance_eval', 'standalone_score', 'standalone_eval'],
    num_rows: 0
})

verifie si huggingface https://huggingface.co/settings/billing
a credit 
creer un df a ton df qui sort pour ne pas perdre du credit